In [1]:
from IPython.core.display import display, HTML

display(HTML("<style>.container { width:100% !important; }</style>")) # Increase cell width
display(HTML("<style>.rendered_html { font-size: 16px; }</style>")) # Increase font size

import warnings
warnings.filterwarnings('ignore')

import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline  

import pandas as pd
import numpy as np
import sklearn

In [2]:
#Loading required Datasets
pm_df = pd.read_csv("~/Desktop/University/IE/Term_II/Machine_Learning_II/Group_HW/power_market.csv")
pm_df.head(5)

fc_demand  fc_nuclear  import_FR  export_FR  fc_wind  fc_solar_pv  \
0    24400.0      7117.2     3000.0     2600.0   1732.0          0.0   
1    23616.0      7117.2     3000.0     2650.0   1826.0          0.0   
2    21893.0      7117.2     3000.0     2650.0   1823.0          0.0   
3    20693.0      7117.2     3000.0     2650.0   1777.0          0.0   
4    19599.0      7117.2     3000.0     2650.0   1746.0          0.0   

   fc_solar_th  price        date  hour  
0          5.1  58.82  2017-01-01     0  
1          0.6  58.23  2017-01-01     1  
2          4.6  51.95  2017-01-01     2  
3          9.7  47.27  2017-01-01     3  
4         24.1  45.49  2017-01-01     4

In [3]:
sc_df = pd.read_csv("~/Desktop/University/IE/Term_II/Machine_Learning_II/Group_HW/scoring.csv")
sc_df.head(5)

fc_demand  fc_nuclear import_FR export_FR  fc_wind  fc_solar_pv  \
0    24744.0      7117.2    2300.0    1750.0   2751.0          0.0   
1    23426.0      7117.2    2300.0    2100.0   2452.0          0.0   
2    22597.0      7117.2    2300.0    2100.0   2060.0          0.0   
3    22285.0      7117.2    2300.0    2100.0   1736.0          0.0   
4    22192.0      7117.2    2300.0    2100.0   1322.0          0.0   

   fc_solar_th        date  hour  
0        627.1  2020-09-01     0  
1        606.6  2020-09-01     1  
2        528.3  2020-09-01     2  
3        598.5  2020-09-01     3  
4        474.9  2020-09-01     4

In [4]:
from pandas_profiling import ProfileReport
report = ProfileReport(pm_df, minimal=False)
report

Summarize dataset:   0%|          | 0/23 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
from pandas_profiling import ProfileReport
report = ProfileReport(sc_df, minimal=False)
report

Summarize dataset:   0%|          | 0/22 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
pm_df.describe()

fc_demand    fc_nuclear     import_FR     export_FR       fc_wind  \
count  32135.000000  32135.000000  32122.000000  32122.000000  32135.000000   
mean   28475.593527   6421.333431   2445.285163   2217.864703   5627.214688   
std     4686.675600    862.355391    623.215136    550.563300   3266.961919   
min    16372.000000   3672.800000    700.000000    200.000000    139.000000   
25%    24605.500000   6071.900000   2100.000000   1900.000000   3083.000000   
50%    28446.000000   7117.200000   2450.000000   2200.000000   4989.000000   
75%    32124.000000   7117.200000   2900.000000   2600.000000   7610.500000   
max    41103.000000   7117.200000   3700.000000   3700.000000  17232.000000   

        fc_solar_pv   fc_solar_th         price          hour  
count  32135.000000  32135.000000  32135.000000  32135.000000  
mean    1100.253546    601.186600     48.440119     11.500296  
std     1512.531532    681.584906     14.842233      6.922199  
min        0.000000      0.000000      0.030000      0.000000  
25%        0.000000     31.600000     39.770000      6.000000  
50%      107.800000    331.400000     49.880000     12.000000  
75%     2099.350000    957.150000     58.250000     17.500000  
max     7211.200000   2253.700000    101.990000     23.000000

In [7]:
pm_df.isnull().sum()

fc_demand       0
fc_nuclear      0
import_FR      13
export_FR      13
fc_wind         0
fc_solar_pv     0
fc_solar_th     0
price           0
date            0
hour            0
dtype: int64

In [8]:
#Filling with last value shown (Motifs: Small Number of missing values + demand should remain fairly stable from one day to the other)
pm_df.fillna(method='ffill', inplace=True)

In [9]:
pm_df.isnull().sum()

fc_demand      0
fc_nuclear     0
import_FR      0
export_FR      0
fc_wind        0
fc_solar_pv    0
fc_solar_th    0
price          0
date           0
hour           0
dtype: int64

In [10]:
#Preliminary feature engeneering: 

#Combining solar energies:
pm_df['fc_solar'] = pm_df['fc_solar_th'] + pm_df['fc_solar_pv'] 

#Creating the aforementioned Thermal Gap:
pm_df['Thermal_Gap'] = pm_df['fc_demand'] - pm_df['fc_nuclear'] - pm_df['fc_wind'] - pm_df['fc_solar']

#Creating Energy Trade Balance SPAIN/FR
pm_df['BoT_FR'] = pm_df['export_FR'] - pm_df['import_FR']

pm_df.head(5)

fc_demand  fc_nuclear  import_FR  export_FR  fc_wind  fc_solar_pv  \
0    24400.0      7117.2     3000.0     2600.0   1732.0          0.0   
1    23616.0      7117.2     3000.0     2650.0   1826.0          0.0   
2    21893.0      7117.2     3000.0     2650.0   1823.0          0.0   
3    20693.0      7117.2     3000.0     2650.0   1777.0          0.0   
4    19599.0      7117.2     3000.0     2650.0   1746.0          0.0   

   fc_solar_th  price        date  hour  fc_solar  Thermal_Gap  BoT_FR  
0          5.1  58.82  2017-01-01     0       5.1      15545.7  -400.0  
1          0.6  58.23  2017-01-01     1       0.6      14672.2  -350.0  
2          4.6  51.95  2017-01-01     2       4.6      12948.2  -350.0  
3          9.7  47.27  2017-01-01     3       9.7      11789.1  -350.0  
4         24.1  45.49  2017-01-01     4      24.1      10711.7  -350.0

In [11]:
pm_df = pm_df.drop(columns = ['import_FR','export_FR','fc_solar_pv','fc_solar_th'], axis = 1)
pm_df.head(5)

fc_demand  fc_nuclear  fc_wind  price        date  hour  fc_solar  \
0    24400.0      7117.2   1732.0  58.82  2017-01-01     0       5.1   
1    23616.0      7117.2   1826.0  58.23  2017-01-01     1       0.6   
2    21893.0      7117.2   1823.0  51.95  2017-01-01     2       4.6   
3    20693.0      7117.2   1777.0  47.27  2017-01-01     3       9.7   
4    19599.0      7117.2   1746.0  45.49  2017-01-01     4      24.1   

   Thermal_Gap  BoT_FR  
0      15545.7  -400.0  
1      14672.2  -350.0  
2      12948.2  -350.0  
3      11789.1  -350.0  
4      10711.7  -350.0

In [12]:
type(pm_df)

pandas.core.frame.DataFrame